# PDE-Net求解对流扩散方程

## 概述

PDE-Net是Zichao Long等人提出的一种前馈深度网络用于从数据中学习偏微分方程，同时实现了准确预测复杂系统的动力学特性和揭示潜在的PDE模型。PDE-Net的基本思想是通过学习卷积核(滤波器)来逼近微分算子，并应用神经网络或其他机器学习方法来拟合未知的非线性响应。数值实验表明，即使在噪声环境中，该模型也可以识别被观测的动力学方程，并预测相对较长时间的动态行为。更多信息可参考[PDE-Net: Learning PDEs from Data](https://arxiv.org/abs/1710.09668)。

本案例要求**MindSpore版本 >= 2.0.0**以调用如下接口: *mindspore.jit, mindspore.jit_class, mindspore.data_sink*。

## 问题描述

本案例求解可变参数的对流-扩散偏微分方程的反问题，并实现长期预测。

## 控制方程

在本研究中，对流扩散方程的形式为：

$$
u_t = a(x,y) u_x + b(x,y) u_y + c u_{xx} + d u_{yy}, \quad (x,y) \in[0,2 \pi] \times[0,2 \pi]
$$

$$
u|_{t=0} = u_0(x,y)
$$

各项导数的系数分别为：

$$
a(x,y)=0.5(cos(y)+x(2\pi-x)sin(x))+0.6 \quad
b(x,y)=2(cos(y)+sin(x))+0.8
$$

$$
c=0.2 \quad
d=0.3
$$


## PDE-Net的模型结构

PDE-Net由多个$\delta T$ Block串联构成，以实现长序列信息的预测，在每一个$\delta T$ Block中，包含可训练参数的moment矩阵，该矩阵可根据映射关系转化为对应导数的卷积核，从而获取物理场的导数。将导数及其对应物理量经线性组合后，采用前向欧拉法，即可推导下一个时间步的信息。

![](images/pdenet-1.jpg)

![](images/pdenet-2.jpg)

## 技术路径

MindFlow求解该问题的具体流程如下：

1. 构建模型。
2. 单步训练。
3. 多步训练。
4. 模型推理及可视化。

In [1]:
import os
import time
import numpy as np

import mindspore
from mindspore.common import set_seed
from mindspore import nn, Tensor, context, ops, jit
from mindspore.train.serialization import load_param_into_net

In [2]:
from mindflow.cell import PDENet
from mindflow.utils import load_yaml_config
from mindflow.loss import get_loss_metric, RelativeRMSELoss
from mindflow.pde import UnsteadyFlowWithLoss

from src import init_model, create_dataset, calculate_lp_loss_error
from src import make_dir, scheduler, get_param_dic
from src import plot_coe, plot_extrapolation_error, get_label_coe, plot_test_error

In [3]:
set_seed(0)
np.random.seed(0)
context.set_context(mode=context.GRAPH_MODE, device_target="GPU", device_id=0)

In [ ]:
# load configuration yaml
config = load_yaml_config('pde_net.yaml')
config["kernel_size"]=5
config["summary_dir"] = "./summary_dir/summary_kernel_5"
config["mindrecord_data_dir"] = "./data5"

## 构建模型

MindFlow提供了`PDENet`接口可以直接建立PDENet模型，需指定网格的宽度、高度、数据深度、边界条件、拟合的最高阶数等信息。

In [5]:
def init_model(config):
    return PDENet(height=config["mesh_size"],
                  width=config["mesh_size"],
                  channels=config["channels"],
                  kernel_size=config["kernel_size"],
                  max_order=config["max_order"],
                  dx=2 * np.pi / config["mesh_size"],
                  dy=2 * np.pi / config["mesh_size"],
                  dt=config["dt"],
                  periodic=config["perodic_padding"],
                  enable_moment=config["enable_moment"],
                  if_fronzen=config["if_frozen"],
                  )

## 单步训练

由于每个$\delta T$ Block的参数是共享的，因此模型根据$\delta T$ Block的串联个数依次增加，逐一进行训练。其中，在step为1时，模型处于warm-up阶段，PDE-Net的moment为“frozen”状态，此时moment中的参数不参与训练。每新增一个$\delta T$ Block，程序先进行数据生成和数据集的读取，初始化模型后，需载入前一个step训练的checkpoint，并定义优化器、模式、loss函数，并进行模型训练，在训练中模型会实时反映模型性能。

训练流程:
1. 模型初始化: 调用 `init_model` 初始化 `PDENet`。
2. 预训练模型加载:
    * 如果 `step` 为 1，则设置模型 `if_fronzen=True`，并使用 `warm_up_epoch_scale` 倍的 `epoch` 进行预热训练。
    * 如果 `step` 大于 1，则加载前一个 `step` 的训练好的模型参数作为当前 `step` 的初始化。
3. 优化器设置: 使用 `nn.Adam` 优化器。
4. 问题定义: 实例化 `UnsteadyFlowWithLoss`，指定 `t_out` 为当前的 `step`。
5. 前向传播与梯度计算: 定义 `forward_fn` 计算损失，并使用 `ops.value_and_grad` 创建 `grad_fn` 来获取损失和梯度。
6. 训练步函数: 使用 `@jit` 装饰器定义 `train_step` 函数，执行单次训练步的计算和参数更新。
7. 数据下沉: 使用 `mindspore.data_sink` 优化数据处理流程。
8. 训练循环:
    * 迭代 `epoch` 次。
    * 每个 `epoch` 内迭代 `train_dataset` 中的所有批次。
    * 打印当前 `epoch` 的训练损失和每 `epoch`/每步的训练时间。
    * 每隔 `config["save_epoch_interval"]` 个 `epoch` 保存模型检查点。
    * 每隔 `config['eval_interval']` 个 `epoch` 在 `eval_dataset` 上评估模型性能（调用 `calculate_lp_loss_error`）。

In [6]:
def train_single_step(step, config, lr, train_dataset, eval_dataset):
    """train PDE-Net with advancing steps"""

    print("Current step for train loop: {}".format(step, ))
    model = init_model(config)

    epoch = config["epochs"]
    warm_up_epoch_scale = 10
    if step == 1:
        model.if_fronzen = True
        epoch = warm_up_epoch_scale * epoch
    elif step == 2:
        param_dict = get_param_dic(config["summary_dir"], step - 1, epoch * 10)
        load_param_into_net(model, param_dict)
        print("Load pre-trained model successfully")
    else:
        param_dict = get_param_dic(config["summary_dir"], step - 1, epoch)
        load_param_into_net(model, param_dict)
        print("Load pre-trained model successfully")

    optimizer = nn.Adam(model.trainable_params(), learning_rate=Tensor(lr))
    problem = UnsteadyFlowWithLoss(model, t_out=step, loss_fn=RelativeRMSELoss(), data_format="NTCHW")

    def forward_fn(u0, uT):
        loss = problem.get_loss(u0, uT)
        return loss

    grad_fn = ops.value_and_grad(forward_fn, None, optimizer.parameters, has_aux=False)

    @jit
    def train_step(u0, uT):
        loss, grads = grad_fn(u0, uT)
        loss = ops.depend(loss, optimizer(grads))
        return loss

    steps = train_dataset.get_dataset_size()
    sink_process = mindspore.data_sink(train_step, train_dataset, sink_size=1)

    for cur_epoch in range(epoch):
        local_time_beg = time.time()
        model.set_train()

        for _ in range(steps):
            cur_loss = sink_process()
            print("epoch: %s, loss is %s" % (cur_epoch + 1, cur_loss), flush=True)
        local_time_end = time.time()
        epoch_seconds = (local_time_end - local_time_beg) * 1000
        step_seconds = epoch_seconds / steps
        print("Train epoch time: {:5.3f} ms, per step time: {:5.3f} ms".format
              (epoch_seconds, step_seconds), flush=True)

        if (cur_epoch + 1) % config["save_epoch_interval"] == 0:
            ckpt_file_name = "ckpt/step_{}".format(step)
            ckpt_dir = os.path.join(config["summary_dir"], ckpt_file_name)
            if not os.path.exists(ckpt_dir):
                make_dir(ckpt_dir)
            ckpt_name = "pdenet-{}.ckpt".format(cur_epoch + 1, )
            mindspore.save_checkpoint(model, os.path.join(ckpt_dir, ckpt_name))

        if (cur_epoch + 1) % config['eval_interval'] == 0:
            calculate_lp_loss_error(problem, eval_dataset, config["batch_size"])

## 多步训练

PDE-Net是逐步进行训练。
使用**MindSpore>= 2.0.0**的版本，可以使用函数式编程范式训练神经网络。

训练流程:
1.  初始化学习率 `lr` 为 `config["lr"]`。
2.  循环从 `1` 到 `config["multi_step"]`（包含 `config["multi_step"]`）：
    * 构建当前训练步的数据库文件名 `db_name`，格式为 `"train_step{}.mindrecord"`，其中 `{}` 为当前循环的 `i` 值。
    * 调用 `create_dataset` 函数创建数据集，参数包括 `config`、当前的 `i` 值、`db_name`、`"train"` 模式以及 `data_size` 为 `2 * config["batch_size"]`。
    * 从创建的 `dataset` 中获取 `train_dataset` 和 `eval_dataset`。
    * 调用 `scheduler` 函数更新学习率 `lr`，传入的调度步长为 `config["multi_step"] / config["learning_rate_reduce_times"]` 的整数部分，当前步数为 `i`，以及当前的学习率 `lr`。
    * 调用 `train_single_step` 函数进行单步训练，参数包括当前的 `step=i`、`config`、更新后的 `lr`、`train_dataset` 和 `eval_dataset`。

In [7]:
def train(config):
    lr = config["lr"]
    for i in range(1, config["multi_step"] + 1):
        db_name = "train_step{}.mindrecord".format(i)
        dataset = create_dataset(config, i, db_name, "train", data_size=2 * config["batch_size"])
        train_dataset, eval_dataset = dataset.create_train_dataset()
        lr = scheduler(int(config["multi_step"] / config["learning_rate_reduce_times"]), step=i, lr=lr)
        train_single_step(step=i, config=config, lr=lr, train_dataset=train_dataset, eval_dataset=eval_dataset)


In [ ]:
if not os.path.exists(config["mindrecord_data_dir"]):
    make_dir(config["mindrecord_data_dir"])
train(config)

[WARNING] ME(607775:140698755004096,MainProcess):2025-06-15-21:05:10.767.877 [mindspore/dataset/engine/datasets.py:1145] Dataset is shuffled before split.


Mindrecorder saved
Current step for train loop: 1
epoch: 1, loss is 316.3384
Train epoch time: 8490.574 ms, per step time: 8490.574 ms
epoch: 2, loss is 285.58875
Train epoch time: 26.613 ms, per step time: 26.613 ms
epoch: 3, loss is 294.71906
Train epoch time: 11.206 ms, per step time: 11.206 ms
epoch: 4, loss is 302.8824
Train epoch time: 20.553 ms, per step time: 20.553 ms
epoch: 5, loss is 298.4911
Train epoch time: 15.071 ms, per step time: 15.071 ms
epoch: 6, loss is 291.5742
Train epoch time: 9.656 ms, per step time: 9.656 ms
epoch: 7, loss is 299.95258
Train epoch time: 13.223 ms, per step time: 13.223 ms
epoch: 8, loss is 272.8629
Train epoch time: 10.689 ms, per step time: 10.689 ms
epoch: 9, loss is 300.99677
Train epoch time: 10.930 ms, per step time: 10.930 ms
epoch: 10, loss is 272.9209
Train epoch time: 10.388 ms, per step time: 10.388 ms
================================Start Evaluation================================
LpLoss_error: 16.021706
============================

[WARNING] ME(607775:140698755004096,MainProcess):2025-06-15-21:06:37.506.426 [mindspore/dataset/engine/datasets.py:1145] Dataset is shuffled before split.


Mindrecorder saved
Current step for train loop: 2
Load pre-trained model successfully
epoch: 1, loss is 0.85283023
Train epoch time: 9010.598 ms, per step time: 9010.598 ms
epoch: 2, loss is 1.0346112
Train epoch time: 20.275 ms, per step time: 20.275 ms
epoch: 3, loss is 0.85627514
Train epoch time: 21.270 ms, per step time: 21.270 ms
epoch: 4, loss is 0.77566737
Train epoch time: 22.120 ms, per step time: 22.120 ms
epoch: 5, loss is 0.7408211
Train epoch time: 21.334 ms, per step time: 21.334 ms
epoch: 6, loss is 0.7285292
Train epoch time: 20.125 ms, per step time: 20.125 ms
epoch: 7, loss is 0.69430816
Train epoch time: 23.145 ms, per step time: 23.145 ms
epoch: 8, loss is 0.702212
Train epoch time: 16.703 ms, per step time: 16.703 ms
epoch: 9, loss is 0.6708083
Train epoch time: 15.520 ms, per step time: 15.520 ms
epoch: 10, loss is 0.61920595
Train epoch time: 15.414 ms, per step time: 15.414 ms
================================Start Evaluation================================
LpLo

[WARNING] ME(607775:140698755004096,MainProcess):2025-06-15-21:07:06.732.70 [mindspore/dataset/engine/datasets.py:1145] Dataset is shuffled before split.


...

[WARNING] MD(607775,7ff3a1fff700,python):2025-06-15-21:15:46.592.799 [mindspore/ccsrc/minddata/dataset/engine/datasetops/batch_op.cc:136] operator()] Memory consumption is more than 87.6069%, which may cause OOM. Please reduce num_parallel_workers size / optimize 'per_batch_map' function / other python data preprocess function to reduce memory usage.
[WARNING] MD(607775,7ff3a1fff700,python):2025-06-15-21:15:46.669.545 [mindspore/ccsrc/minddata/dataset/engine/datasetops/batch_op.cc:136] operator()] Memory consumption is more than 87.6066%, which may cause OOM. Please reduce num_parallel_workers size / optimize 'per_batch_map' function / other python data preprocess function to reduce memory usage.
[WARNING] MD(607775,7ff3a1fff700,python):2025-06-15-21:15:46.740.832 [mindspore/ccsrc/minddata/dataset/engine/datasetops/batch_op.cc:136] operator()] Memory consumption is more than 87.6046%, which may cause OOM. Please reduce num_parallel_workers size / optimize 'per_batch_map' function / oth

epoch: 7, loss is 0.9708165
Train epoch time: 76.373 ms, per step time: 76.373 ms
epoch: 8, loss is 0.9330128
Train epoch time: 79.761 ms, per step time: 79.761 ms
epoch: 9, loss is 0.9148545
Train epoch time: 90.020 ms, per step time: 90.020 ms


[WARNING] MD(607775,7ff3a1fff700,python):2025-06-15-21:15:46.818.058 [mindspore/ccsrc/minddata/dataset/engine/datasetops/batch_op.cc:136] operator()] Memory consumption is more than 87.6048%, which may cause OOM. Please reduce num_parallel_workers size / optimize 'per_batch_map' function / other python data preprocess function to reduce memory usage.
[WARNING] MD(607775,7ff3a1fff700,python):2025-06-15-21:15:46.902.476 [mindspore/ccsrc/minddata/dataset/engine/datasetops/batch_op.cc:136] operator()] Memory consumption is more than 87.6165%, which may cause OOM. Please reduce num_parallel_workers size / optimize 'per_batch_map' function / other python data preprocess function to reduce memory usage.
[WARNING] MD(607775,7ff3a1fff700,python):2025-06-15-21:15:46.990.261 [mindspore/ccsrc/minddata/dataset/engine/datasetops/batch_op.cc:136] operator()] Memory consumption is more than 87.6324%, which may cause OOM. Please reduce num_parallel_workers size / optimize 'per_batch_map' function / oth

epoch: 10, loss is 0.90370035
Train epoch time: 70.486 ms, per step time: 70.486 ms
================================Start Evaluation================================


[WARNING] MD(607775,7ff5b17fe700,python):2025-06-15-21:15:47.071.453 [mindspore/ccsrc/minddata/dataset/engine/datasetops/batch_op.cc:136] operator()] Memory consumption is more than 87.6172%, which may cause OOM. Please reduce num_parallel_workers size / optimize 'per_batch_map' function / other python data preprocess function to reduce memory usage.
[WARNING] MD(607775,7ff5b17fe700,python):2025-06-15-21:15:47.072.432 [mindspore/ccsrc/minddata/dataset/engine/datasetops/batch_op.cc:136] operator()] Memory consumption is more than 87.6172%, which may cause OOM. Please reduce num_parallel_workers size / optimize 'per_batch_map' function / other python data preprocess function to reduce memory usage.
[WARNING] MD(607775,7ff5b17fe700,python):2025-06-15-21:15:47.073.143 [mindspore/ccsrc/minddata/dataset/engine/datasetops/batch_op.cc:136] operator()] Memory consumption is more than 87.6172%, which may cause OOM. Please reduce num_parallel_workers size / optimize 'per_batch_map' function / oth